Task: Text Analysis of 10-k filing using LLM inference API

Installating dependencies


In [1]:
!pip install langchain-core
!pip install langchain-community

In [2]:
! pip install chromadb

In [3]:
! pip install langchain

In [4]:
!pip install -U sec-edgar-downloader

Load dataset

In [8]:
import langchain
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_community.document_loaders import TextLoader
from langchain.schema.document import Document
from typing import List

In [52]:
from sec_edgar_downloader import Downloader
import os
import re
from bs4 import BeautifulSoup
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import nltk
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\tvish\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\tvish\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [6]:
dl = Downloader("MyCompanyName", "my.email@domain.com")

In [9]:
# ticker_symbols = ["T", "VZ", "TMUS"]
# output_directory = "/content/sec-edgar-filings"
# for ticker in ticker_symbols:
#     dl.get("10-K", ticker, after="1995-01-01", before="2024-01-01")

In [13]:
output_directory = 'C:\\Users\\tvish\sec-edgar-filings'


In [14]:
ticker = "TMUS"  # Specify the ticker symbol for the company you want to retrieve data for

folder_path = os.path.join(output_directory, ticker, "10-K")
filing_folders = os.listdir(folder_path)

if filing_folders:
    filing_folders.sort()
    first_filing_folder = os.path.join(folder_path, filing_folders[0])
    filing_files = os.listdir(first_filing_folder)

    if filing_files:
        filing_files.sort()

        first_file_path = os.path.join(first_filing_folder, filing_files[0])

        with open(first_file_path, 'r') as file:
            file_contents = file.read()
            print(f"Contents of the first file in {ticker}:")
            print(file_contents)
            print("---------------------------------------------")
    else:
        print(f"No files found inside the first filing folder for {ticker}")
else:
    print(f"No filing folders found for {ticker}")


Contents of the first file in TMUS:
-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 LDLlftLztYl7M4OLd/KoyJuuFD+nPGkUo0yInjxYWi4sqrdQoU3pesMhUWyGKAWW
 FKrVwrHv81Ft7yBLPMmnFg==

<SEC-DOCUMENT>0000950134-07-007079.txt : 20070330
<SEC-HEADER>0000950134-07-007079.hdr.sgml : 20070330
<ACCEPTANCE-DATETIME>20070330155053
ACCESSION NUMBER:		0000950134-07-007079
CONFORMED SUBMISSION TYPE:	10-K
PUBLIC DOCUMENT COUNT:		7
CONFORMED PERIOD OF REPORT:	20061231
FILED AS OF DATE:		20070330
DATE AS OF CHANGE:		20070330

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			METROPCS COMMUNICATIONS INC
		CENTRAL INDEX KEY:			0001283699
		STANDARD INDUSTRIAL CLASSIFICATION:	RADIO TELEPHONE COMMUNICATIONS [4812]
		IRS NUMBER:				000000000

	FILING VALUES:
		FORM TYPE:		10-K
		SEC 

Exploring the data

In [15]:
doc_start_pattern = re.compile(r'<DOCUMENT>')
doc_end_pattern = re.compile(r'</DOCUMENT>')
# Regex to find <TYPE> tag prceeding any characters, terminating at new line
type_pattern = re.compile(r'<TYPE>[^\n]+')

In [17]:
doc_start_is = [x.end() for x in doc_start_pattern.finditer(file_contents)]
doc_end_is = [x.start() for x in doc_end_pattern.finditer(file_contents)]
doc_types = [x[len('<TYPE>'):] for x in type_pattern.findall(file_contents)]

In [18]:
document = {}

for doc_type, doc_start, doc_end in zip(doc_types, doc_start_is, doc_end_is):
    if doc_type == '10-K':
        document[doc_type] = file_contents[doc_start:doc_end]

In [19]:
regex = re.compile(r'(>Item(\s|&#160;|&nbsp;)(1|1A|1B|7A|7|8)\.{0,1})|(ITEM\s(1A|1B|7A|7|8))')

# Use finditer to math the regex
matches = regex.finditer(document['10-K'])

for match in matches:
    print(match)

<re.Match object; span=(10155, 10168), match='>Item&nbsp;1.'>
<re.Match object; span=(10596, 10608), match='>Item&nbsp;1'>
<re.Match object; span=(11042, 11054), match='>Item&nbsp;1'>
<re.Match object; span=(14322, 14335), match='>Item&nbsp;7.'>
<re.Match object; span=(14846, 14860), match='>Item&nbsp;7A.'>
<re.Match object; span=(15339, 15352), match='>Item&nbsp;8.'>
<re.Match object; span=(17675, 17687), match='>Item&nbsp;1'>
<re.Match object; span=(18164, 18176), match='>Item&nbsp;1'>
<re.Match object; span=(18621, 18633), match='>Item&nbsp;1'>
<re.Match object; span=(19148, 19160), match='>Item&nbsp;1'>
<re.Match object; span=(19651, 19663), match='>Item&nbsp;1'>
<re.Match object; span=(20554, 20566), match='>Item&nbsp;1'>
<re.Match object; span=(36577, 36590), match='>Item&nbsp;1.'>
<re.Match object; span=(237506, 237518), match='>Item&nbsp;1'>
<re.Match object; span=(385144, 385156), match='>Item&nbsp;1'>
<re.Match object; span=(474209, 474222), match='>Item&nbsp;7.'>
<re.Match o

In [20]:
import pandas as pd
matches = regex.finditer(document['10-K'])

test_df = pd.DataFrame([(x.group(), x.start(), x.end()) for x in matches])

test_df.columns = ['item', 'start', 'end']
test_df['item'] = test_df.item.str.lower()

test_df.head()

item  start    end
0   >item&nbsp;1.  10155  10168
1    >item&nbsp;1  10596  10608
2    >item&nbsp;1  11042  11054
3   >item&nbsp;7.  14322  14335
4  >item&nbsp;7a.  14846  14860

In [21]:
test_df.replace('&#160;',' ',regex=True,inplace=True)
test_df.replace('&nbsp;',' ',regex=True,inplace=True)
test_df.replace(' ','',regex=True,inplace=True)
test_df.replace('\.','',regex=True,inplace=True)
test_df.replace('>','',regex=True,inplace=True)

test_df.head()

item  start    end
0   item1  10155  10168
1   item1  10596  10608
2   item1  11042  11054
3   item7  14322  14335
4  item7a  14846  14860

In [22]:
pos_dat = test_df.sort_values('start', ascending=True).drop_duplicates(subset=['item'], keep='last')

pos_dat

item    start      end
15   item7   474209   474222
16  item7a   928058   928072
17   item8   930026   930039
23   item1  1290811  1290823

In [23]:
pos_dat.set_index('item', inplace=True)

pos_dat

start      end
item                    
item7    474209   474222
item7a   928058   928072
item8    930026   930039
item1   1290811  1290823

In [24]:
# Get Item 7
item_7_raw = document['10-K'][pos_dat['start'].loc['item7']:pos_dat['start'].loc['item7a']]

# Get Item 7a
item_7a_raw = document['10-K'][pos_dat['start'].loc['item7a']:pos_dat['start'].loc['item8']]

In [25]:
item_7a_raw[:1000]

'>Item&nbsp;7A. </B><B><I>Quantitative and Qualitative Disclosures About Market Risk</I></B>\n</DIV>\n\n\n<DIV align="left" style="font-size: 10pt; margin-top: 6pt">&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;Market risk is the potential loss arising from adverse changes in market prices and rates,\nincluding interest rates. We do not routinely enter into derivatives or other financial instruments\nfor trading, speculative or hedging purposes, unless it is required by our credit agreements. We do\nnot currently conduct business internationally, so we are generally not subject to foreign currency\nexchange rate risk.\n</DIV>\n\n\n<DIV align="left" style="font-size: 10pt; margin-top: 6pt">&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;&nbsp;As of December&nbsp;31, 2006, we had approximately $1.6&nbsp;billion in outstanding indebtedness under\nour senior secured credit facility that bears interest at floating rates based on the London Inter\nBank Offered Rate, or LI

In [26]:
item_7a_content = BeautifulSoup(item_7a_raw, 'lxml')

In [27]:
print(item_7a_content.get_text("\n\n")[0:1500])

>Item 7A. 

Quantitative and Qualitative Disclosures About Market Risk




          Market risk is the potential loss arising from adverse changes in market prices and rates,
including interest rates. We do not routinely enter into derivatives or other financial instruments
for trading, speculative or hedging purposes, unless it is required by our credit agreements. We do
not currently conduct business internationally, so we are generally not subject to foreign currency
exchange rate risk.





          As of December 31, 2006, we had approximately $1.6 billion in outstanding indebtedness under
our senior secured credit facility that bears interest at floating rates based on the London Inter
Bank Offered Rate, or LIBOR, plus 2.50%. The interest rate on the outstanding debt under our senior
secured credit facility as of December 31, 2006 was 7.875%. On November 21, 2006, to manage our
interest rate risk exposure and fulfill a requirement of our senior secured credit facility, we
enter

In [29]:
# content = BeautifulSoup(document_all, 'lxml')

In [30]:
# print(content.get_text("\n\n"))

Preprocessing the data

In [31]:
def preprocess_text(text):
  content = BeautifulSoup(text, 'lxml')
  clean_text=content.get_text("\n\n")
  clean_text = re.sub(r'\.{2,}', '', clean_text)
  preprocessed_text = re.sub(r'-{2,}', '', clean_text)
  return preprocessed_text

In [32]:
output_dir = 'C:\\Users\\tvish\sec-edgar-filings\preprocessed_data'
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

In [34]:
base_dir = 'C:\\Users\\tvish\sec-edgar-filings'

In [35]:
for ticker in ticker_symbols:
    ticker_directory = os.path.join(base_dir, ticker, "10-K")

    if not os.path.exists(ticker_directory):
        print(f"No filings found for ticker symbol {ticker}")
        continue

    for root, dirs, files in os.walk(ticker_directory):
        for dir_name in dirs:
            dir_path = os.path.join(root, dir_name)
            full_submission_file = os.path.join(dir_path, "full-submission.txt")
            if os.path.exists(full_submission_file):
                # Read the content of the full submission file
                with open(full_submission_file, 'r', encoding='utf-8') as infile:
                    content = infile.read()
                    # Extract metadata
                    filed_as_of_date = re.search(r'FILED AS OF DATE:\s+(\d+)', content)
                    company_conformed_name = re.search(r'COMPANY CONFORMED NAME:\s+(.*?)\s+', content)
                    if filed_as_of_date:
                        filing_date = filed_as_of_date.group(1)
                    else:
                        filing_date = "Unknown"
                    if company_conformed_name:
                        company_name = company_conformed_name.group(1)
                    else:
                        company_name = "Unknown"
                    # Set metadata
                    metadata = f"Company Name: {company_name}\nFiling Date: {filing_date}\n\n"
                    doc_text=preprocess_text(content)
                    # Create a new document with the preprocessed content and metadata
                    new_document = metadata + doc_text
                    output_file = os.path.join(output_directory, f"{ticker}_{dir_name}_{filing_date}.txt")
                    with open(output_file, 'w', encoding='utf-8') as outfile:
                        outfile.write(new_document)


Preparing the data for LLM

In [4]:
pip install typing-inspect==0.8.0 typing_extensions==4.5.0

  Using cached typing_extensions-4.5.0-py3-none-any.whl.metadata (8.5 kB)
Using cached typing_extensions-4.5.0-py3-none-any.whl (27 kB)
  Attempting uninstall: typing_extensions
    Found existing installation: typing_extensions 4.11.0
    Uninstalling typing_extensions-4.11.0:
      Successfully uninstalled typing_extensions-4.11.0
Note: you may need to restart the kernel to use updated packages.


DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spyder 4.2.5 requires pyqt5<5.13, which is not installed.
spyder 4.2.5 requires pyqtwebengine<5.13, which is not installed.
sqlalchemy 2.0.30 requires typing-extensions>=4.6.0, but you have typing-extensions 4.5.0 which is incompatible.
chromadb 0.5.0 requires numpy>=1.22.5, but you have numpy 1.22.4 which is incompatible.
fastapi 0.111.0 requires typing-extensions>=4.8.0, but you have typing-extensions 4.5.0 which is incompatible.
nbclassic 0.2.6 requires jupyter-server~=1

In [5]:
pip install pydantic -U

  Using cached pydantic-2.7.1-py3-none-any.whl.metadata (107 kB)
  Using cached typing_extensions-4.11.0-py3-none-any.whl.metadata (3.0 kB)
Using cached pydantic-2.7.1-py3-none-any.whl (409 kB)
Using cached typing_extensions-4.11.0-py3-none-any.whl (34 kB)
  Attempting uninstall: typing-extensions
    Found existing installation: typing_extensions 4.5.0
    Uninstalling typing_extensions-4.5.0:
      Successfully uninstalled typing_extensions-4.5.0
  Attempting uninstall: pydantic
    Found existing installation: pydantic 1.10.11
    Uninstalling pydantic-1.10.11:
      Successfully uninstalled pydantic-1.10.11
Note: you may need to restart the kernel to use updated packages.


DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063
  You can safely remove it manually.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spyder 4.2.5 requires pyqt5<5.13, which is not installed.
spyder 4.2.5 requires pyqtwebengine<5.13, which is not installed.
chromadb 0.5.0 requires numpy>=1.22.5, but you have numpy 1.22.4 which is incompatible.
farm-haystack 1.25.5 requires pydantic<2, but you have pydantic 2.7.1 which is incompatible.
nbclassic 0.2.6 requires jupyter-server~=1.1, but you have jupyter-server 2.14.0 which is incompatible.
nbclassic 0.2.6 requires noteboo

In [6]:
pip install pydantic==1.10.11

  Using cached pydantic-1.10.11-cp38-cp38-win_amd64.whl.metadata (150 kB)
Using cached pydantic-1.10.11-cp38-cp38-win_amd64.whl (2.2 MB)
  Attempting uninstall: pydantic
    Found existing installation: pydantic 2.7.1
    Uninstalling pydantic-2.7.1:
      Successfully uninstalled pydantic-2.7.1
Note: you may need to restart the kernel to use updated packages.


DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
chromadb 0.5.0 requires numpy>=1.22.5, but you have numpy 1.22.4 which is incompatible.


In [7]:
pip install langchain

Note: you may need to restart the kernel to use updated packages.


DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [9]:
import os

In [10]:
directory_path = "C:\\Users\\tvish\sec-edgar-filings"

docs = []

for filename in os.listdir(directory_path):
    if filename.endswith(".txt"):
        with open(os.path.join(directory_path, filename), "r", encoding="utf-8") as file:
            content = file.read()
            if isinstance(content, str):
                doc = Document(page_content=content)
                docs.append(doc)
            else:
                print(f"Skipping file {filename} as its content is not a string.")

In [11]:
docs[1]


Document(page_content='Company Name: METROPCS\nFiling Date: 20080229\n\nBEGIN PRIVACY-ENHANCED MESSAGE\nProc-Type: 2001,MIC-CLEAR\nOriginator-Name: webmaster@www.sec.gov\nOriginator-Key-Asymmetric:\n MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen\n TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB\nMIC-Info: RSA-MD5,RSA,\n CHmB5d3TEMjU5dQk5VD3KkiEG1OycHZxMjOk4lI4V491B9iS7lNTbVNx5ejTukOm\n f6Fx6T6+dpyKtYNA9pR+cA==\n\n\n\n0000950134-08-003844.txt : 20080229\n\n\n0000950134-08-003844.hdr.sgml : 20080229\n\n\n20080229162639\nACCESSION NUMBER:\t\t0000950134-08-003844\nCONFORMED SUBMISSION TYPE:\t10-K\nPUBLIC DOCUMENT COUNT:\t\t10\nCONFORMED PERIOD OF REPORT:\t20071231\nFILED AS OF DATE:\t\t20080229\nDATE AS OF CHANGE:\t\t20080229\n\nFILER:\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tMETROPCS COMMUNICATIONS INC\n\t\tCENTRAL INDEX KEY:\t\t\t0001283699\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tRADIO TELEPHONE COMMUNICATIONS [4812]\n\t\tIRS NUMBER:\t\t\t\t200

In [12]:
print (f'You have {len(docs)} document(s) in your data')
print (f'There are {len(docs[0].page_content)} characters in your sample document')
print (f'Here is a sample: {docs[0].page_content[:200]}')

You have 69 document(s) in your data
There are 1011720 characters in your sample document
Here is a sample: Company Name: METROPCS
Filing Date: 20070330

BEGIN PRIVACY-ENHANCED MESSAGE
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2


In [13]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=50)
texts = text_splitter.split_documents(docs)

In [14]:
print (f'Now you have {len(texts)} documents')

Now you have 391996 documents


In [15]:
metadata_list = []

for doc in docs:
    # Extract metadata from the document content
    metadata = {}
    lines = doc.page_content.split('\n') if '\n' in doc.page_content else doc.page_content.split('\r\n')
    for line in lines:
        if line.startswith('Company Name:'):
            metadata['Company Name'] = line.split(':', 1)[1].strip()
        elif line.startswith('Filing Date:'):
            metadata['Filing Date'] = line.split(':', 1)[1].strip()
    metadata_list.append(metadata)


# Split documents into text chunks
text_splitter = RecursiveCharacterTextSplitter(chunk_size=8000, chunk_overlap=20)
text_chunks = text_splitter.split_documents(docs)  # Accessing 'page_content'

# Verify lengths
print(len(metadata_list))  # Number of documents
print(len(text_chunks))


69
45851


Setting up Ollama

Vector Embedding

In [44]:
!ollama pull nomic-embed-text


pulling manifest â ‹ pulling manifest â ¹ pulling manifest â ¸ pulling manifest â ¼ pulling manifest â ´ pulling manifest â ´ pulling manifest â § pulling manifest â § pulling manifest â � pulling manifest â � pulling manifest â ™ pulling manifest â ™ pulling manifest â ¹ pulling manifest â ¼ pulling manifest â ¼ pulling manifest â ¦ pulling manifest â ¦ pulling manifest â § pulling manifest â � pulling manifest 
pulling 970aa74c0a90... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–� 274 MB                         
pulling c71d239df917... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–�  11 KB                         
pulling ce4a164fc046... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–�   17 B                         
pulling 31df23ea7daa... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–�  420 B                         
verifying sha256 digest â ‹ pulling manifest 
pulling 970aa74c0a90... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–

In [56]:
!pip install huggingface_hub
!pip install pinecone-client

DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


   ---------------------------------------- 0.0/214.5 kB ? eta -:--:--
   ---------------------------------------- 214.5/214.5 kB 6.6 MB/s eta 0:00:00


DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [46]:
# install package
!pip install -U langchain-nomic

     ---------------------------------------- 0.0/43.6 kB ? eta -:--:--
     ---------------------------------------- 43.6/43.6 kB 2.1 MB/s eta 0:00:00
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Installing backend dependencies: started
  Installing backend dependencies: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
   ---------------------------------------- 0.0/62.5 kB ? eta -:--:--
   ---------------------------------------- 62.5/62.5 kB 3.3 MB/s eta 0:00:00
   ---------------------------------------- 0.0/25.9 MB ? eta -:--:--
    --------------------------------------- 0.4/25.9 MB 8.9 MB/s eta 0:00:03
   - -------------------------------------- 1.2/25.9 MB 10.7 MB/s eta 0:00:03
   -- ---------------------------------

DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [17]:
from langchain_nomic.embeddings import NomicEmbeddings

embeddings = NomicEmbeddings(model="nomic-embed-text-v1.5")

In [19]:
from langchain.vectorstores import Pinecone
import os
from langchain_community.embeddings import OllamaEmbeddings
import pinecone


In [20]:
PINECONE_API_KEY = os.environ.get('PINECONE_API_KEY', '14480b48-5f50-4277-814b-f5e011641821')
PINECONE_API_ENV = os.environ.get('PINECONE_API_ENV', 'asia-southeast1-gcp-free')

In [21]:
embedding=OllamaEmbeddings(model="nomic-embed-text",show_progress=True),

In [22]:
!pip install -U langchain-pinecone

DEPRECATION: pyodbc 4.0.0-unsupported has a non-standard version number. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of pyodbc or contact the author to suggest that they release a version with a conforming version number. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [23]:
from pinecone import Pinecone
pc = Pinecone(api_key='14480b48-5f50-4277-814b-f5e011641821')
index = pc.Index("10k-vectors")

In [92]:
from langchain_community.embeddings import OllamaEmbeddings
from pinecone import Pinecone
import numpy as np
import uuid

# Initialize OllamaEmbeddings with the model name
ollama_emb = OllamaEmbeddings(model="nomic-embed-text", show_progress=True)

# Initialize Pinecone client 
pc = Pinecone(api_key='14480b48-5f50-4277-814b-f5e011641821')

# Define the namespace and index name
index_name = "10k-vectors"

index = pc.Index(index_name)

chunk_size = 1000

# Iterate over text chunks, embed them, and store in Pinecone
for i in range(0, len(text_chunks), chunk_size):
    chunk_embeddings = []
    chunk_metadata = []
    # Embed a chunk of text chunks
    for chunk_text, metadata in zip(text_chunks[i:i + chunk_size], metadata_list[i:i + chunk_size]):
        # Embed document
        embedding = ollama_emb.embed_query(chunk_text)
        chunk_embeddings.append(embedding)
        
        # Prepare metadata
        metadata = {"company_name": metadata["Company Name"], "file_name": metadata["Filing Date"]}  
        chunk_metadata.append(metadata)

    # Upsert vectors with metadata into the Pinecone index
    index.upsert(vectors=[{"id": str(uuid.uuid4()), "values": embedding, "metadata": metadata} 
                           for embedding, metadata in zip(chunk_embeddings, chunk_metadata)])

print("Embeddings with metadata stored successfully in Pinecone.")





OllamaEmbeddings:   0%|                                                                          | 0/1 [00:00<?, ?it/s]


OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:35<00:00, 35.27s/it]



OllamaEmbeddings:   0%|                                                                          | 0/1 [00:00<?, ?it/s]


OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:29<00:00, 29.01s/it]



OllamaEmbeddings:   0%|                                                                          | 0/1 [00:00<?, ?it/s]


OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:17<00:00, 17.98s/it]



OllamaEmbeddings:   0%|                                                                          | 0/1 [00:00<?, ?it/s]


OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:24<00:00, 24.27s/it]



OllamaEmbeddings:

PineconeApiException: (400)
Reason: Bad Request
HTTP response headers: HTTPHeaderDict({'Date': 'Sat, 11 May 2024 08:49:51 GMT', 'Content-Type': 'application/json', 'Content-Length': '52', 'Connection': 'keep-alive', 'x-pinecone-request-latency-ms': '34', 'x-pinecone-request-id': '6105310171250200699', 'x-envoy-upstream-service-time': '34', 'server': 'envoy'})
HTTP response body: {"code":3,"message":"Invalid request.","details":[]}


Retrieval

In [7]:
from langchain.prompts import ChatPromptTemplate, PromptTemplate
from langchain_core.output_parsers import StrOutputParser
from langchain_community.chat_models import ChatOllama
from langchain_core.runnables import RunnablePassthrough
from langchain.retrievers.multi_query import MultiQueryRetriever

In [85]:
# pip install farm-haystack

In [86]:
# pip install nomic

In [25]:
!ollama pull mistral

pulling manifest â ‹ pulling manifest â ™ pulling manifest â ¹ pulling manifest â ¼ pulling manifest â ¼ pulling manifest â ´ pulling manifest â § pulling manifest â § pulling manifest â ‡ pulling manifest â � pulling manifest â ‹ pulling manifest â ™ pulling manifest â ¸ pulling manifest â ¸ pulling manifest â ¼ pulling manifest â ¦ pulling manifest â ¦ pulling manifest â § pulling manifest â ‡ pulling manifest â ‹ pulling manifest â ‹ pulling manifest â ¹ pulling manifest â ¸ pulling manifest â ¸ pulling manifest â ´ pulling manifest â ´ pulling manifest â § pulling manifest â § pulling manifest â � pulling manifest 
pulling e8a35b5937a5... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–� 4.1 GB                         
pulling 43070e2d4e53... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–�  11 KB                         
pulling e6836092461f... 100% â–•â–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–ˆâ–�   42 B                         
pulling ed11eda7790d... 1

In [26]:
local_model = "mistral"
llm = ChatOllama(model=local_model)

In [27]:
QUERY_PROMPT = PromptTemplate(
    input_variables=["question"],
    template="""You are an AI language model assistant tasked with analysing financial data from 10-k filings. Your goal is to provide finanical insights about the performace of the companies based on their filings. {question}""",
)

In [8]:
from langchain_pinecone import PineconeVectorStore


In [137]:
from langchain_pinecone import PineconeVectorStore
os.environ['PINECONE_API_KEY'] = '14480b48-5f50-4277-814b-f5e011641821'
vectorstore_from_docs = PineconeVectorStore.from_documents(
        text_chunks,
        index_name='10k-2',
        embedding=ollama_emb
    )


OllamaEmbeddings: 100%|█████████████████████████████████████████████████████████| 1000/1000 [12:46:49<00:00, 46.01s/it]

OllamaEmbeddings:   2%|█                                                          | 19/1000 [13:11<17:15:26, 63.33s/it]

KeyboardInterrupt: 

In [59]:
from langchain_pinecone import PineconeVectorStore
os.environ['PINECONE_API_KEY'] = '14480b48-5f50-4277-814b-f5e011641821'
index_name_text='10k-2'
vectorstore = PineconeVectorStore.from_existing_index(index_name_text, embeddings)

In [60]:
    retriever = MultiQueryRetriever.from_llm(
        vectorstore.as_retriever(),
        llm,
        prompt=QUERY_PROMPT
    )
    
    # RAG prompt
    template = """Answer the question based ONLY on the following context:
    {context}
    Question: {question}
    """
    
    prompt = ChatPromptTemplate.from_template(template)

In [61]:
chain = (
    {"context": retriever, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

In [62]:
from langchain.retrievers.multi_query import MultiQueryRetriever
retriever = MultiQueryRetriever.from_llm(
    retriever=vectorstore.as_retriever(), llm=llm
)

In [63]:
import logging

logging.basicConfig()
logging.getLogger("langchain.retrievers.multi_query").setLevel(logging.INFO)

In [64]:
import nomic
nomic.login('nk-dD9GIercvRsRCqP-V52mBcZWWGsvks0q57lgTla0pzk')

Prompts

In [65]:
risk_tmobile="Identify risk factors of T-mobile from 1995 to 2024?"
risk_answer_tmobile= chain.invoke("Identify risk factors of T-mobile from 1995 to 2024?")
risk_answer_tmobile

INFO:langchain.retrievers.multi_query:Generated queries: ['Analyzing financial risk factors for a company like T-Mobile, which has a long history and goes through various transformations over the years, requires an in-depth analysis of its annual reports or 10-K filings from 1995 to 2024. Although I cannot directly access these documents, I can suggest potential risk factors based on common themes that have historically impacted telecommunications companies. Some of the risks T-Mobile may have faced during this period include:', '', "1. Regulatory Risk: Telecommunications is a heavily regulated industry, and changes in regulations or enforcement actions can significantly impact a company's operations and financial performance.", '2. Competitive Risk: Intense competition in the telecom market from both established players and new entrants, particularly in the wireless sector, can put downward pressure on prices, revenues, and profitability.', '3. Economic Risk: A weak or uncertain econo

" I. Introduction:\nT-Mobile US, Inc. is a subsidiary of Deutsche Telekom AG, a German telecommunications company. The following is a list of potential risks that T-Mobile faced during the period from 1995 to 2024, although please note that this list is not exhaustive and some risks may have varied in significance over time:\n\nII. Regulatory Risks:\n1. Government regulations and policies regarding wireless communication, spectrum allocation, and competition (e.g., net neutrality rules, merger approval) could impact T-Mobile's business operations and growth plans.\n2. Fines or penalties for noncompliance with laws and regulations, such as those related to data privacy and consumer protection.\n\nIII. Infrastructure Risks:\n1. Development and maintenance of a robust network infrastructure to support increasing demand for wireless services and keep up with competitors (e.g., 5G rollout).\n2. Dependence on third-party vendors and partnerships for technology, equipment, and network expansi

In [66]:
risk_att="Give Organization And Summary Of Significant Accounting Policies [Line Items] values"
risk_answer_att= chain.invoke(risk_att)
risk_answer_att

INFO:langchain.retrievers.multi_query:Generated queries: ['Title: Financial Insights from Significant Accounting Policies in 10-K Filings', '', 'Introduction:', "In this analysis, I will be reviewing the significant accounting policies disclosed by companies in their 10-K filings and providing insights into their financial performance based on these policies. The focus will be on line items that have a material impact on a company's financial statements.", '', 'I. Organization:', 'A. Company Overview: Provide a brief description of the business and industry in which the company operates.', 'B. Corporate Structure: Determine if there are any subsidiaries or affiliated entities, and how they are accounted for.', 'C. Fiscal Year: Identify the fiscal year end and how it impacts seasonality or industry trends.', '', 'II. Summary of Significant Accounting Policies (Line Items):', '1. Revenue Recognition: Understanding how a company recognizes revenue, such as over the course of production or

' Title: Significant Accounting Policies of the Organization\n\n1. Revenue Recognition: We follow the revenue recognition principle based on the completion of a sale or performance of a service. Revenue is recognized in the statement of operations when the following criteria are met: (i) persuasive evidence of an arrangement exists, (ii) delivery has occurred or services have been performed, and (iii) collectability is reasonably assured.\n\n2. Expense Recognition: We recognize expenses in the period in which they are incurred. Costs associated with long-term assets are capitalized and expensed over their useful lives using the straight-line method, unless another method is more appropriate.\n\n3. Materiality: Accounting policies are applied consistently for material items and adjustments to prior periods are made when necessary.\n\n4. Use of Estimates: Management uses its best judgment in making estimates and recognizes a liability or asset when it is probable that a future economic b

Another method for RAG 

In [12]:
def extract_answer(embedded_query, embeddings):
    pc = Pinecone(api_key='14480b48-5f50-4277-814b-f5e011641821')
    index_name = "10k-2"
    index = pc.Index(index_name)
    result = index.query(vector=embedded_query, top_k=10)
    ids = [match['id'] for match in result['matches']]
    texts = []
    for id in ids:
        # Fetch the metadata for each ID
        metadata = index.fetch(ids=[id])['vectors'][id]['metadata']
        text = metadata.get('text', '')
        texts.append(text)
    return texts

In [4]:
def generate_response(context, query):
    PROMPT_TEMPLATE = """
    Answer the question based only on the following context:

    {context}

    ---

    Answer the question based on the above context: {question}
    """
    context_text = ",".join(str(element) for element in context)
    prompt_template = ChatPromptTemplate.from_template(PROMPT_TEMPLATE)
    prompt = prompt_template.format(context=context_text, question=query)
    model = Ollama(model="llama3")
    response = model.invoke(prompt)
    return response

In [5]:
def get_embeddings(articles, embeddings):
    return embeddings.embed_documents(texts=articles)

In [11]:
from langchain_community.llms.ollama import Ollama
embeddings = OllamaEmbeddings(model="nomic-embed-text", show_progress=True)

query="Identify risk factors of Verizon from 1995 to 2024?"
embed = get_embeddings([query], embeddings)
query_context = extract_answer(embed, embeddings)
query_answer = generate_response(query_context, query)
print("Query answer:", query_answer)


OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:18<00:00, 18.74s/it]


Query answer: I think there may be a mistake in your request!

The provided context is about MetroPCS Communications, Inc. and Subsidiaries, not Verizon. Additionally, it appears that this information only relates to financial statements from 2006 to 2008.

If you meant to ask about risk factors of Verizon, I'd need more information or a different context to provide an answer.

Please clarify or provide additional context, and I'll be happy to help!


In [43]:
query="Retrive Selected financial data tables for MetroPCS Communicationsof 1995,1996,1997,1998,2000,2001,2002,2003"
embed = get_embeddings([query], embeddings)
query_context = extract_answer(embed, embeddings)

OllamaEmbeddings: 100%|██████████████████████████████████████████████████████████████████| 1/1 [00:03<00:00,  3.97s/it]


In [44]:
query_context

['$\n\n\n\n\n3,412,403\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n$\n\n\n\n\n646,641\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n$\n\n\n\n\n(2,607,051\n\n\n\n\n)\n\n\n\n\n\xa0\n\n\n\n\n$\n\n\n\n\n5,806,130\n\n\n\n\n\xa0\n\n\n\n\n\n\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\n\n\n\n\n\nCURRENT LIABILITIES:\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n\n\n\n\n\n\nAccounts payable and\naccrued expenses\n\n\n\n\n\xa0\n\n\n\n\n$\n\n\n\n\n77\n\n\n\n\n\xa0\n\n\n\n\n\xa0\n\n\n\n\n$\n

In [45]:
query_answer = generate_response(query_context, query)
print("Query answer:", query_answer)

Query answer: I apologize, but there is no financial data table for MetroPCS Communications of 1995, 1996, 1997, or 1998. The provided context only includes notes to consolidated financial statements for the years 2004, 2003, and 2002.

However, I can retrieve selected financial data tables for MetroPCS Communications of 2000, 2001, 2002, 2003, and 2004 from the context:

**Table: Selected Financial Data (MetroPCS Communications)**

| Year | Revenue | Net Income |
| --- | --- | --- |
| 2000 | $435.8 million | $(34.9) million |
| 2001 | $543.7 million | $(32.2) million |
| 2002 | $642.5 million | $(26.6) million |
| 2003 | $771.4 million | $(12.5) million |
| 2004 | $942.9 million | $42.1 million |

Please note that these tables only include revenue and net income data for the specified years. If you need more detailed information or data for other years, please let me know!
